In [1]:
import serial
from pandas import DataFrame
import gc
gc.enable()

SYNC = 0xaa
EXCODE = 0x55
Bytes_per_data = 2

In [2]:
com_port = input('com_port:')
Duration_Time = int(input('Duration Time(miniute):')) 
Recorded_Time = int(input('Recorded Time(miniute):')) 
sample_freq = int(input('Sample Frequency(hz):'))
baud_rate = int(input('Baud Rate:'))  #57600
timeout = int(input('Timeout:'))

com_port:com5
Duration Time(miniute):3
Recorded Time(miniute):1
Sample Frequency(hz):512
Baud Rate:57600
Timeout:3


In [3]:
def TOCSV():
    digital_raw = []
    for i in range(0, len(signals), Bytes_per_data):
        value = signals[i] * 256 + signals[i + 1]
        if value >= 32768:
            value = value - 65536
            digital_raw.append(value)
        else:
            digital_raw.append(value)
        del value
        
    gc.collect()
    df_digital_raw = DataFrame(digital_raw)
    df_digital_raw.to_csv('digital_raw.csv',index=False,header=False)

In [4]:
def reconnect():
    try:
        stream = serial.Serial(com_port, baud_rate , timeout = timeout )
        print("串列埠詳情引數：", stream)
        signals = []
        readTGAM()
            
    except:
        print ('Error connection' )
        print('Please shutdown and Reopen')
        stream.close()
        input()

In [5]:
def parsepayload(payload, plength):

    bytesParsed = 0

    while (bytesParsed < plength):
        extendedCodeLevel = 0

        while (payload[bytesParsed] == EXCODE):
            extendedCodeLevel = extendedCodeLevel + 1
            bytesParsed = bytesParsed + 1

        code = payload[bytesParsed]

        if (code > 0x7F):
            bytesParsed = bytesParsed + 1
            length = payload[bytesParsed]
            if (code == 0x80):
                for i in range(length):
                    signals.append(payload[bytesParsed + 1 + i])
                    print("signals data(16):%X \n" % signals[-1])
        else:
            length = 1

        bytesParsed = bytesParsed + length + 1


In [6]:
def readTGAM():
    
    while True:
        sync_1 = stream.read(1)
        if (sync_1[0] != SYNC): continue

        sync_2 = stream.read(1)
        if (sync_2[0] != SYNC): continue

        while True:
            plength = stream.read(1)
            if (plength[0] != 170): break

        if (plength[0] > 169): continue

        # Decodeing
        payload = stream.read(plength[0])
        checksum = 0
        for i in range(plength[0]):
            checksum = checksum + payload[i]
        checksum &= 0xFF
        checksum = ~checksum & 0xFF

        chk = stream.read(1)
        if (chk[0] != checksum): continue

        if len(signals) < Duration_Time*60*sample_freq*2:
            parsepayload(payload, plength[0])
            if (len(signals) % (Recorded_Time*60*sample_freq*2) == 0 ):
                TOCSV()
                print('%d min is done' %Recorded_Time)
        else:
            break
            
    TOCSV()
    print('done')
    stream.close()
    input()

In [ ]:
try:
    global stream
    stream = serial.Serial(com_port, baud_rate , timeout = timeout )
    print("串列埠詳情引數：", stream)
    signals = []
    readTGAM()
        
except KeyboardInterrupt:
    stream.close()
    TOCSV()
    print('error')
    input()

except OSError:
    print('OSError')
    print('Reconnect...')
    stream.close()
    reconnect()


串列埠詳情引數： Serial<id=0x2334fc6df28, open=True>(port='com5', baudrate=57600, bytesize=8, parity='N', stopbits=1, timeout=3, xonxoff=False, rtscts=False, dsrdtr=False)
signals data(16):0 

signals data(16):12 

signals data(16):0 

signals data(16):C 

signals data(16):0 

signals data(16):11 

signals data(16):0 

signals data(16):C 

signals data(16):0 

signals data(16):A 

signals data(16):0 

signals data(16):1C 

signals data(16):0 

signals data(16):37 

signals data(16):0 

signals data(16):35 

signals data(16):0 

signals data(16):2B 

signals data(16):0 

signals data(16):34 

signals data(16):0 

signals data(16):35 

signals data(16):0 

signals data(16):28 

signals data(16):0 

signals data(16):13 

signals data(16):0 

signals data(16):6 

signals data(16):0 

signals data(16):3 

signals data(16):0 

signals data(16):2 

signals data(16):0 

signals data(16):4 

signals data(16):0 

signals data(16):10 

signals data(16):0 

signals data(16):21 

signals data(16):0 

signa

signals data(16):0 

signals data(16):1A 

signals data(16):0 

signals data(16):1A 

signals data(16):0 

signals data(16):1D 

signals data(16):0 

signals data(16):29 

signals data(16):0 

signals data(16):34 

signals data(16):0 

signals data(16):34 

signals data(16):0 

signals data(16):34 

signals data(16):0 

signals data(16):34 

signals data(16):0 

signals data(16):37 

signals data(16):0 

signals data(16):30 

signals data(16):0 

signals data(16):30 

signals data(16):0 

signals data(16):3C 

signals data(16):0 

signals data(16):38 

signals data(16):0 

signals data(16):2B 

signals data(16):0 

signals data(16):30 

signals data(16):0 

signals data(16):41 

signals data(16):0 

signals data(16):3A 

signals data(16):0 

signals data(16):1C 

signals data(16):0 

signals data(16):9 

signals data(16):0 

signals data(16):5 

signals data(16):0 

signals data(16):19 

signals data(16):0 

signals data(16):26 

signals data(16):0 

signals data(16):1C 

signals data(

signals data(16):0 

signals data(16):2D 

signals data(16):0 

signals data(16):29 

signals data(16):0 

signals data(16):28 

signals data(16):0 

signals data(16):25 

signals data(16):0 

signals data(16):22 

signals data(16):0 

signals data(16):15 

signals data(16):0 

signals data(16):0 

signals data(16):FF 

signals data(16):F3 

signals data(16):FF 

signals data(16):F6 

signals data(16):0 

signals data(16):A 

signals data(16):0 

signals data(16):21 

signals data(16):0 

signals data(16):21 

signals data(16):0 

signals data(16):18 

signals data(16):0 

signals data(16):1C 

signals data(16):0 

signals data(16):2D 

signals data(16):0 

signals data(16):39 

signals data(16):0 

signals data(16):41 

signals data(16):0 

signals data(16):38 

signals data(16):0 

signals data(16):25 

signals data(16):0 

signals data(16):17 

signals data(16):0 

signals data(16):13 

signals data(16):0 

signals data(16):16 

signals data(16):0 

signals data(16):B 

signals data

signals data(16):0 

signals data(16):4A 

signals data(16):0 

signals data(16):42 

signals data(16):0 

signals data(16):3C 

signals data(16):0 

signals data(16):39 

signals data(16):0 

signals data(16):33 

signals data(16):0 

signals data(16):2C 

signals data(16):0 

signals data(16):23 

signals data(16):0 

signals data(16):22 

signals data(16):0 

signals data(16):2C 

signals data(16):0 

signals data(16):24 

signals data(16):0 

signals data(16):14 

signals data(16):0 

signals data(16):C 

signals data(16):0 

signals data(16):16 

signals data(16):0 

signals data(16):2B 

signals data(16):0 

signals data(16):38 

signals data(16):0 

signals data(16):2A 

signals data(16):0 

signals data(16):19 

signals data(16):0 

signals data(16):23 

signals data(16):0 

signals data(16):31 

signals data(16):0 

signals data(16):34 

signals data(16):0 

signals data(16):23 

signals data(16):0 

signals data(16):16 

signals data(16):0 

signals data(16):5 

signals data(

signals data(16):0 

signals data(16):8 

signals data(16):0 

signals data(16):1 

signals data(16):0 

signals data(16):14 

signals data(16):0 

signals data(16):35 

signals data(16):0 

signals data(16):41 

signals data(16):0 

signals data(16):25 

signals data(16):0 

signals data(16):13 

signals data(16):0 

signals data(16):1A 

signals data(16):0 

signals data(16):34 

signals data(16):0 

signals data(16):45 

signals data(16):0 

signals data(16):3D 

signals data(16):0 

signals data(16):34 

signals data(16):0 

signals data(16):37 

signals data(16):0 

signals data(16):31 

signals data(16):0 

signals data(16):21 

signals data(16):0 

signals data(16):14 

signals data(16):0 

signals data(16):D 

signals data(16):0 

signals data(16):C 

signals data(16):0 

signals data(16):10 

signals data(16):0 

signals data(16):17 

signals data(16):0 

signals data(16):28 

signals data(16):0 

signals data(16):39 

signals data(16):0 

signals data(16):43 

signals data(16

...

signals data(16):0 

signals data(16):36 

signals data(16):0 

signals data(16):29 

signals data(16):0 

signals data(16):33 

signals data(16):0 

signals data(16):3A 

signals data(16):0 

signals data(16):2D 

signals data(16):0 

signals data(16):16 

signals data(16):0 

signals data(16):10 

signals data(16):0 

signals data(16):13 

signals data(16):0 

signals data(16):20 

signals data(16):0 

signals data(16):22 

signals data(16):0 

signals data(16):26 

signals data(16):0 

signals data(16):21 

signals data(16):0 

signals data(16):11 

signals data(16):FF 

signals data(16):FE 

signals data(16):FF 

signals data(16):EF 

signals data(16):FF 

signals data(16):EE 

signals data(16):0 

signals data(16):6 

signals data(16):0 

signals data(16):27 

signals data(16):0 

signals data(16):32 

signals data(16):0 

signals data(16):41 

signals data(16):0 

signals data(16):50 

signals data(16):0 

signals data(16):48 

signals data(16):0 

signals data(16):3C 

signals d

signals data(16):0 

signals data(16):23 

signals data(16):0 

signals data(16):30 

signals data(16):0 

signals data(16):29 

signals data(16):0 

signals data(16):26 

signals data(16):0 

signals data(16):23 

signals data(16):0 

signals data(16):16 

signals data(16):0 

signals data(16):22 

signals data(16):0 

signals data(16):39 

signals data(16):0 

signals data(16):45 

signals data(16):0 

signals data(16):44 

signals data(16):0 

signals data(16):3B 

signals data(16):0 

signals data(16):35 

signals data(16):0 

signals data(16):38 

signals data(16):0 

signals data(16):31 

signals data(16):0 

signals data(16):1B 

signals data(16):0 

signals data(16):6 

signals data(16):FF 

signals data(16):FB 

signals data(16):FF 

signals data(16):F6 

signals data(16):0 

signals data(16):C 

signals data(16):0 

signals data(16):1D 

signals data(16):0 

signals data(16):22 

signals data(16):0 

signals data(16):2C 

signals data(16):0 

signals data(16):39 

signals dat

signals data(16):0 

signals data(16):23 

signals data(16):0 

signals data(16):1D 

signals data(16):0 

signals data(16):1A 

signals data(16):0 

signals data(16):18 

signals data(16):0 

signals data(16):1A 

signals data(16):0 

signals data(16):23 

signals data(16):0 

signals data(16):32 

signals data(16):0 

signals data(16):3B 

signals data(16):0 

signals data(16):38 

signals data(16):0 

signals data(16):30 

signals data(16):0 

signals data(16):2B 

signals data(16):0 

signals data(16):28 

signals data(16):0 

signals data(16):25 

signals data(16):0 

signals data(16):22 

signals data(16):0 

signals data(16):1B 

signals data(16):0 

signals data(16):15 

signals data(16):0 

signals data(16):10 

signals data(16):0 

signals data(16):18 

signals data(16):0 

signals data(16):1A 

signals data(16):0 

signals data(16):8 

signals data(16):0 

signals data(16):8 

signals data(16):0 

signals data(16):21 

signals data(16):0 

signals data(16):2C 

signals data(

signals data(16):0 

signals data(16):C 

signals data(16):0 

signals data(16):25 

signals data(16):0 

signals data(16):32 

signals data(16):0 

signals data(16):33 

signals data(16):0 

signals data(16):2B 

signals data(16):0 

signals data(16):23 

signals data(16):0 

signals data(16):2B 

signals data(16):0 

signals data(16):39 

signals data(16):0 

signals data(16):48 

signals data(16):0 

signals data(16):49 

signals data(16):0 

signals data(16):3D 

signals data(16):0 

signals data(16):42 

signals data(16):0 

signals data(16):53 

signals data(16):0 

signals data(16):52 

signals data(16):0 

signals data(16):3B 

signals data(16):0 

signals data(16):21 

signals data(16):0 

signals data(16):14 

signals data(16):0 

signals data(16):2C 

signals data(16):0 

signals data(16):48 

signals data(16):0 

signals data(16):47 

signals data(16):0 

signals data(16):3A 

signals data(16):0 

signals data(16):30 

signals data(16):0 

signals data(16):30 

signals data

signals data(16):0 

signals data(16):25 

signals data(16):0 

signals data(16):1D 

signals data(16):0 

signals data(16):1B 

signals data(16):0 

signals data(16):21 

signals data(16):0 

signals data(16):21 

signals data(16):0 

signals data(16):12 

signals data(16):FF 

signals data(16):FE 

signals data(16):FF 

signals data(16):F9 

signals data(16):0 

signals data(16):8 

signals data(16):0 

signals data(16):2A 

signals data(16):0 

signals data(16):45 

signals data(16):0 

signals data(16):40 

signals data(16):0 

signals data(16):2A 

signals data(16):0 

signals data(16):15 

signals data(16):0 

signals data(16):7 

signals data(16):FF 

signals data(16):FE 

signals data(16):FF 

signals data(16):EF 

signals data(16):FF 

signals data(16):F4 

signals data(16):0 

signals data(16):0 

signals data(16):FF 

signals data(16):FE 

signals data(16):0 

signals data(16):C 

signals data(16):0 

signals data(16):30 

signals data(16):0 

signals data(16):3A 

signals d